# Generating plots from the NINAPRO data and classifier results

In [1]:
from deepconvlstm import session_run
import plotly.graph_objs as go
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import pickle
import matplotlib.pyplot as plt
from scipy import signal
from __future__ import division
import numpy as np
from nina_helper import *
import scipy.fftpack
init_notebook_mode(connected=True)

  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


In [2]:
HIST_PATH = '../results/history/db1/ts200/'
subject = 3
with open(HIST_PATH+'subject:{}_history.pickle'.format(subject), 'rb') as hfile:
    data = pickle.load(hfile)
max_idx = data['val_acc'].index(max(data['val_acc']))
max_val = data['val_acc'][max_idx:max_idx+1]
max_x = [max_idx, max_idx+1]
layout = go.Layout(
    title = 'Subject {} - database 1 training curve (validation accuracy)'.format(subject),
    xaxis = {'title': 'Epoch'},
    yaxis = {'title': 'Validation Accuracy'})
iplot({'data': [{'y': data['val_acc'],'name': 'val_acc'},
                {'y': signal.savgol_filter(data['val_acc'], 43, 3), 
                 'name': 'smoothed val_acc'},
                {'y': max_val, 'x': max_x, 'mode': 'markers',
                 'marker':{'size': 10, 'symbol': 'star-triangle-up'}, 'name': 'Max value'},
               ],
       'layout': layout})

In [3]:
db2_path = "../databases/db2"
db2_func = nina_helper.import_db2
db2_freq = 2000
db3_path = "../databases/db3"
db3_func = nina_helper.import_db3
db3_freq = db2_freq
subject = 10
# Number of samplepoints
N = 10000

def plot_spectral(num_points, subject, import_func, db_path, freq):
    data_dict = import_func(db_path, subject)
    # sample spacing
    T = 1.0 / freq
    layout = go.Layout(
        title = 'Subject {} power spectral density'.format(subject),
        xaxis = {'title': 'Frequency (Hz)'},
        yaxis = {'title': 'Power'})
    data_plot = {'layout': layout, 'data': []}
    xf = np.linspace(0.0, 1.0/(2.0*T), N)
    for i in range(data_dict['emg'].shape[1]):
        if i != 11:
            continue
        y = data_dict['emg'][:,i][0:N]

        #yf = abs(scipy.fftpack.fft(y))**2
        yf = scipy.fftpack.fft(y)
        data_plot['data'].append({'y': 2.0/N * np.abs(yf[:N//2]),
                                  'name': 'Channel {}'.format(i+1), 'x': xf})
    iplot(data_plot)

def get_splot(num_points, subject, import_func, db_path, freq, chans=[11]):
    data_dict = import_func(db_path, subject)
    layout = go.Layout(
        title = 'Subject {} power spectral density'.format(subject),
        xaxis = {'title': 'Frequency (Hz)'},
        yaxis = {'title': 'Power'})
    data_plot = {'layout': layout, 'data': []}
    for i in chans:
        y = data_dict['emg'][:,i][0:N]
        yf = scipy.fftpack.fft(y)
        data_plot['data'].append({'y': 2.0/N * np.abs(yf[:N//2]),
                                  'name': 'Channel {}'.format(i+1), 'x': xf})
    iplot(data_plot)    
    
data_dict = db3_func(db3_path, subject)
y = data_dict['emg'][:,11][0:N]
f, Pxx_den = signal.periodogram(y, db3_freq)
layout = go.Layout(
        title = 'Comparision of Power Spectral Density',
        xaxis = {'title': 'Frequency (Hz)'},
        yaxis = {'title': 'Power Spectral Density(W/Hz)'})
data_plot = {'layout': layout, 'data': []}
subject = 4
data_dict = db2_func(db2_path, subject)
y = data_dict['emg'][:,11][0:N]
f, Pxx_den = signal.periodogram(y, db2_freq)
data_plot['data'].append({'y': signal.savgol_filter(Pxx_den, 43, 5),
                          'name': 'Database 2 - Subject {}'.format(subject), 'x': f})
subject = 6
data_dict = db2_func(db2_path, subject)
y = data_dict['emg'][:,11][0:N]
f, Pxx_den = signal.periodogram(y, db2_freq)
data_plot['data'].append({'y': signal.savgol_filter(Pxx_den, 43, 5),
                          'name': 'Database 2 - Subject {}'.format(subject), 'x': f})
subject = 4
data_dict = db3_func(db3_path, subject)
y = data_dict['emg'][:,11][0:N]
f, Pxx_den = signal.periodogram(y, db3_freq)
data_plot['data'].append({'y': signal.savgol_filter(Pxx_den, 43, 5),
                          'name': 'Database 3 - Subject {}'.format(subject), 'x': f})
subject = 6
data_dict = db3_func(db3_path, subject)
y = data_dict['emg'][:,11][0:N]
f, Pxx_den = signal.periodogram(y, db3_freq)
data_plot['data'].append({'y': signal.savgol_filter(Pxx_den, 43, 5),
                          'name': 'Database 3 - Subject {}'.format(subject), 'x': f})
iplot(data_plot)


In [4]:
layout = go.Layout(
    title = 'Database 3 - Subject {} sEMG visualization'.format(subject),
    xaxis = {'title': 'Time (seconds)','nticks': 20},
    yaxis = {'title': 'sEMG (Volts)', 'range': [-0.00017, 0.00015]})
data_plot = {'layout': layout, 'data': []}
subject = 4
duration = 500
N = db2_freq*duration
data_dict = db3_func(db3_path, subject)
y = data_dict['emg'][:,11][0:N][680000:720000]
x = np.linspace(340, 360, num=len(y), endpoint=False)
data_plot['data'].append({'y': y,
                          'name': 'Database 3 - Subject 4', 'x': x})
iplot(data_plot)
